In [1]:
# import libraries
import numpy as np
import plotly.express as px 
import cv2 as cv 
import skimage as ski
from skimage.color import rgb2hsv, hsv2rgb

In [2]:
# take the image in RGB
""" rgb_img = ski.io.imread("jackets.jpeg") """
rgb_img = ski.io.imread("parrot.jpg")

img = px.imshow(rgb_img)
img.show() 

# convert the image in HSV
hsv_img = rgb2hsv(rgb_img)

In [3]:
# Function that converts a hsv image into a gray_scale hsv image
def gray_scale(hsv):
    hsv_grayScale = np.copy(hsv)
    hsv_grayScale[:, :, 1] = 0  
    return hsv_grayScale

# get the image's gray scale
grayScale_img = gray_scale(hsv_img)
grayScale_img = hsv2rgb(grayScale_img)

img = px.imshow(grayScale_img)
img.show()

In [4]:
def createMaskInRange(hsv, lower_bound, upper_bound):
    mask = np.all((hsv >= lower_bound) & (hsv <= upper_bound), axis=2) # provare a farla direttamente 3d instead of 2d, ma nel caso bisogna modificare anche la applyMask
    return mask

# set the bounds for the selected color
lower_bound = np.array([140,50,50]) # kinda orange: [10,100,120]; kinda blue: [140,50,50]
upper_bound = np.array([160,255,255]) # kinda orange [39,255,255]; kinda blue: [160,255,255]

# convert the hsv image in int values instead of floating point
hsv_img = hsv_img * 255
hsv_img = hsv_img.astype('uint8')

# create a mask using the bounds above
mask = createMaskInRange(hsv_img, lower_bound, upper_bound)

In [5]:
def createInvMask(maskToInv):
    invMask = np.logical_not(maskToInv) # ~ is slower than np.logical_not
    return invMask

# create the inverse of the mask above
invMask = createInvMask(mask)

In [6]:
def applyMask(img, mask):
    mask = mask.astype('uint8')
    mask = np.repeat(mask, 3, axis=1)
    mask = np.reshape(mask, img.shape)
    res = img * mask
    return res

# compute the foreground of the image by applying the mask to the gray scale image
foreground = applyMask(grayScale_img, mask)
img = px.imshow(foreground)
img.show()

In [7]:
# compute the background of the image by applying the inverse mask to the original image
background = applyMask(rgb_img, invMask)

img = px.imshow(background)
img.show()

In [8]:
# convert the float values in int value in a range [0,255]
foreground = foreground * 255
foreground = foreground.astype('uint8')

# compute the final image adding the foreground to the background
finalImg = background + foreground

img = px.imshow(finalImg)
img.show()